# Stalagmites and Stalagmimtes

In [107]:
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
%matplotlib qt

In [434]:
def display(A, fig):
    maxX = A.shape[0]
    maxY = A.shape[1]
    B = np.zeros((maxY, maxX))
    for ix in range(0,maxX):
        for iy in range(0,maxY):
            B[maxY-1-iy,ix] = A[ix,iy]

    #Display the graphics outside of the notebook. 
    #On a PC, use '%matplotlib qt' instead.
    fig.clear()
    ax = fig.gca()
    ax.axis('off')
    ax.imshow(B, vmin=0, vmax=100, cmap=mpl.colors.LinearSegmentedColormap.from_list('cavemap', ['skyblue', 'black', 'tan']))
    plt.draw()
    plt.pause(.005)

In [490]:
class Drop:
    def __init__(self, x, y, mass, drip_rate):
        self.x = x
        self.xOrg = x
        self.y = y
        self.mass = mass
        self.drip_rate = drip_rate   
        self.stal_start = x - 2
        self.stal_end = x + 2
        self.prev_x = x
        self.prev_y = y
        self.prev = 50
        self.blocked = False

    def update(self, cave, maxX, maxY):
        # print("Pos: {0}, {1} ".format(x, y))
        
        # Generate Probabilities. Choose different schemes to see different results.
        r = np.random.rand()
        prob_deposit = 1 / self.mass # Probability droplet deposits material around it. Based on mass of droplet. 
        prob_block = .70              # Probability droplet evaporates and covers tip of straw      
        prob_dir = .5                 # Probability for direction the droplet will flow. 
    
        up = self.y + 1
        down = self.y - 1      
        left = self.x - 1
        right = self.x + 1    

        # Update Drop Position
        if (up != (maxY - 1)):
            cave[self.prev_x, self.prev_y] = self.prev   
            
        # Horizontal position based on normal distribution
        normal = np.round(np.random.normal(0, 1))
            
        if (self.blocked and self.x != (self.xOrg + normal)):
            if (self.x < self.xOrg and cave[self.x + 1, self.y] == 50):
                self.x += 1
            elif (self.x > self.xOrg and (cave[self.x - 1, self.y] == 50)):
                self.x -= 1 

            if (r > prob_deposit and cave[self.x, up] == 100):
                cave[self.x, self.y] = 100              
                if (self.y == (maxY - 2)):
                    if (self.x < self.xOrg):
                        self.stal_start -= 1
                    else:
                        self.stal_end += 1
              
        self.prev = cave[self.x, self.y]
        self.prev_x = self.x
        self.prev_y = self.y
            
        if (cave[self.x, self.y] == 50):
            cave[self.x, self.y] = self.mass
            
        # If drop is hitting a surface  
        if (r > prob_deposit and cave[self.x, down] == 99): 
            self.floor_impact(cave, maxY)
            self.mass = 0    
        else:
            # If droplet is touching the edges of the straw.        
            if (not self.blocked):
                if (cave[left, up] == 100 and cave[right, up] == 100):
                    if (cave[left, self.y] != 100 and cave[right, self.y] != 100):
                        if (self.mass == 1 and r > prob_block):
                            cave[self.x, self.y:] = 100
                            self.mass -= 1
                            self.blocked = True  
                        elif (r > prob_deposit):
                            cave[left, self.y] = 100
                            cave[right, self.y] = 100
                            self.mass -= 1    
                 
        if (self.mass == 0 or cave[self.x, self.y] == 99):
            self.y = maxY - 2
            self.mass = np.random.randint(1, 10)
            if (self.blocked):
                # Going left side
                if (r < prob_dir):
                    self.x = self.stal_start
                # Going right side
                else:
                    self.x = self.stal_end
        else:
            self.y -= 1
                        
    def floor_impact(self, cave, maxY):
        x, y, mass, prev, blocked = self.x, self.y, self.mass, self.prev, self.blocked
        start = x - (mass - 1)
        end = x + mass
        for ix in range(start, end):
            iy = y
            while (cave[ix, iy - 1] != 99):
                iy -= 1
            cave[ix, iy] = 99        

In [495]:
def init_cave(maxX, maxY, num_drops, drop_list):
    cave = 50 * np.ones((maxX, maxY))
    # Create cave ceiling and floor    
    for i in range(maxX):
        cave[i, maxY - 1] = 100 #ceiling
        cave[i, 0] = 99       #floor
        
    # Create num_drops origin points    
    leftLim = maxX // 5
    rightLim = maxX - (maxX // 5)  
    drops_x = np.linspace(leftLim, rightLim, num_drops, dtype=int)  
    drop_list = []
    
    for i in range(num_drops):
        drop = Drop(drops_x[i], maxY - 2, np.random.randint(1, 10), np.random.randint(1, 5))
        drop_list.append(drop)
            
    fig = plt.figure(1) 
    plt.show()   
    return fig, cave, drop_list

In [497]:
from matplotlib.animation import FFMpegWriter
maxX, maxY = 200, 50
iterations = 750
drop_list = []
fig, cave, drop_list = init_cave(maxX, maxY, 4, drop_list)


metadata = dict(title='Formation of Stalactites and Stalagmites', artist='Matplotlib',comment='Stalactite/Stalagmite')
writer = FFMpegWriter(fps=30, metadata=metadata,bitrate=200000)
with writer.saving(fig, "animation.mp4", dpi=200):
    # Multiple drops
    for i in range(iterations):
        for drop in drop_list:
            if (i % drop.drip_rate == 0):
                drop.update(cave, maxX, maxY) 
        display(cave, fig)
        writer.grab_frame()